first I import the libraries I am using, than load the data, and finally setup ydata and display it

In [10]:
from ydata_profiling import ProfileReport # ydata for simple data analysis
import pandas as pd # pandas for reading the dataset and array manipulation
import os # os for paths; specifically current working directory

# get home path than go to the data folder and the data file name
path = os.getcwd() + "\\data\\fire_archive_M-C61_626683.csv.xz"
# load the dataset
data = pd.read_csv(path)

Profiler = ProfileReport(data) # load data into ydata
display(Profiler) # display ydata analysis

Render HTML: 100%|██████████| 1/1 [00:01<00:00,  1.36s/it]


modify acq_date and acq_time into acq_datetime

In [11]:
from datetime import timedelta # import timedelta from datetime to convert hours and minutes to be addable to date

data['acq_date'] = pd.to_datetime(data['acq_date'])
data['acq_datetime'] = data['acq_date'] + pd.Series(
    [timedelta(minutes=i % 100, hours=i // 100) for i in data['acq_time']])

# remove redundant columns.
# acq_time, and acq_date are now one as acq_datetime so they are redundant
data.drop('acq_time', axis=1, inplace=True)
data.drop('acq_date', axis=1, inplace=True)
# everything in the instrument column is the same and thus redundant
data.drop('instrument', axis=1, inplace=True)
# show data after adding datetime and removing redundant columns
data

latitude  longitude  brightness  scan  track satellite  confidence  \
0         38.5422   -78.3047       304.8   2.8    1.6     Terra          23   
1         38.5451   -78.3107       309.9   2.8    1.6     Terra          79   
2         38.5563   -78.3084       309.4   2.8    1.6     Terra          70   
3         38.5586   -78.3170       302.3   2.8    1.6     Terra          45   
4         31.3393   -89.9124       304.9   1.0    1.0     Terra          62   
...           ...        ...         ...   ...    ...       ...         ...   
2960417   41.6966   -99.1437       319.8   1.1    1.0      Aqua          80   
2960418   42.4419   -94.3783       300.6   1.2    1.1      Aqua          40   
2960419   41.4014   -97.9485       319.9   1.0    1.0      Aqua          80   
2960420   41.4032   -97.9369       322.9   1.0    1.0      Aqua          82   
2960421   42.7180  -120.4872       303.0   1.1    1.0      Aqua          51   

         version  bright_t31   frp daynight  type        acq_datetime  
0           6.03       280.9  40.3        N     0 2000-11-01 02:50:00  
1           6.03       280.7  58.8        N     0 2000-11-01 02:50:00  
2           6.03       280.4  54.5        N     0 2000-11-01 02:50:00  
3           6.03       279.8  36.0        N     0 2000-11-01 02:50:00  
4           6.03       287.5   8.5        N     0 2000-11-01 04:27:00  
...          ...         ...   ...      ...   ...                 ...  
2960417    61.03       284.7  21.2        D     0 2025-01-31 20:28:00  
2960418    61.03       284.3   6.3        D     0 2025-01-31 20:28:00  
2960419    61.03       284.9  19.0        D     0 2025-01-31 20:28:00  
2960420    61.03       285.0  22.1        D     0 2025-01-31 20:28:00  
2960421    61.03       281.1   7.8        D     0 2025-01-31 22:07:00  

[2960422 rows x 13 columns]

import functions from statsmodels for VIF

In [12]:
from statsmodels.stats.outliers_influence import variance_inflation_factor
from statsmodels.tools.tools import add_constant

data_vif = add_constant(data) # add constant to data

# convert categorical data to numeric
data_vif['daynight']=data_vif['daynight'].map({'N':0,'D':1})
data_vif['acq_datetime'] = data_vif['acq_datetime'].apply(lambda x: x.toordinal())
data_vif['satellite']=data_vif['satellite'].map({"Terra":0,'Aqua':1})

# setup VIF
vif_data = pd.DataFrame()
vif_data["Feature"] = data_vif.columns
vif_data["VIF"] = [variance_inflation_factor(data_vif.values, i) for i in range(data_vif.shape[1])]

# display VIF
print(vif_data)

         Feature            VIF
0          const  114845.149151
1       latitude       1.834819
2      longitude       2.138221
3     brightness       3.964907
4           scan      30.149526
5          track      30.064461
6      satellite       1.043072
7     confidence       1.760009
8        version       1.263774
9     bright_t31       1.800932
10           frp       2.038557
11      daynight       1.406411
12          type       1.084178
13  acq_datetime       1.274218


import functions from statsmodels for OLS(Ordinary Least Squares) analysis, and run OLS analysis

In [13]:
import statsmodels.api as sm
from statsmodels.tools.tools import add_constant

temp_data = add_constant(data) # add constant

# change categorical to numeric data for analysis
temp_data['daynight']=temp_data['daynight'].map({'N':0,'D':1})
temp_data['acq_datetime'] = temp_data['acq_datetime'].apply(lambda x: x.toordinal())
temp_data['satellite']=temp_data['satellite'].map({"Terra":0,'Aqua':1})

# set dependent variable to confidence and everything else to independent variables
X=temp_data.drop(['confidence'],axis=1)
X=sm.add_constant(X)
y=temp_data['confidence']

# fit OLS model
model=sm.OLS(y,X).fit()

# show model analysis/summary
model.summary()

<class 'statsmodels.iolib.summary.Summary'>
"""
                            OLS Regression Results                            
==============================================================================
Dep. Variable:             confidence   R-squared:                       0.432
Model:                            OLS   Adj. R-squared:                  0.432
Method:                 Least Squares   F-statistic:                 1.875e+05
Date:                Mon, 07 Jul 2025   Prob (F-statistic):               0.00
Time:                        21:39:54   Log-Likelihood:            -1.2654e+07
No. Observations:             2960422   AIC:                         2.531e+07
Df Residuals:                 2960409   BIC:                         2.531e+07
Df Model:                          12                                         
Covariance Type:            nonrobust                                         
================================================================================
                   coef    std err          t      P>|t|      [0.025      0.975]
--------------------------------------------------------------------------------
const          -49.1388      3.423    -14.354      0.000     -55.848     -42.429
latitude        -0.1669      0.001   -129.370      0.000      -0.169      -0.164
longitude        0.0240      0.001     35.387      0.000       0.023       0.025
brightness       0.8158      0.001   1183.600      0.000       0.814       0.817
scan             1.3221      0.068     19.496      0.000       1.189       1.455
track           -0.2031      0.222     -0.914      0.361      -0.639       0.232
satellite       -0.0435      0.021     -2.106      0.035      -0.084      -0.003
version          0.0108      0.001     13.731      0.000       0.009       0.012
bright_t31      -0.2552      0.001   -182.749      0.000      -0.258      -0.252
frp             -0.0268   6.54e-05   -409.766      0.000      -0.027      -0.027
daynight        -8.1159      0.029   -277.468      0.000      -8.173      -8.059
type            -3.5661      0.024   -150.191      0.000      -3.613      -3.520
acq_datetime -7.743e-05   4.63e-06    -16.720      0.000   -8.65e-05   -6.84e-05
==============================================================================
Omnibus:                   817253.063   Durbin-Watson:                   1.656
Prob(Omnibus):                  0.000   Jarque-Bera (JB):          2709000.929
Skew:                          -1.396   Prob(JB):                         0.00
Kurtosis:                       6.764   Cond. No.                     2.49e+08
==============================================================================

Notes:
[1] Standard Errors assume that the covariance matrix of the errors is correctly specified.
[2] The condition number is large, 2.49e+08. This might indicate that there are
strong multicollinearity or other numerical problems.
"""